In [1]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.preprocessing.image import load_img
from tensorflow.keras.preprocessing.image import img_to_array
from tensorflow.keras.applications.vgg16 import preprocess_input
from tensorflow.keras.applications.vgg16 import decode_predictions
# from tensorflow.keras.applications.vgg16 import VGG16


In [2]:
import kagglehub

# Download latest version of dataset
path = kagglehub.dataset_download("michaeljkerr/20k-album-covers-within-20-genres")

print("Path to dataset files:", path)

/opt/miniconda3/envs/neuralnetworks2024/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Path to dataset files: /Users/adrianclement/.cache/kagglehub/datasets/michaeljkerr/20k-album-covers-within-20-genres/versions/1


In [14]:
import pandas as pd
import os

genres = ['Blues', 'Classical', 'Country', 'DeathMetal', 'DoomMetal', 'DrumNBass', 'Electronic', 'Folk', 'Grime', 'HeavyMetal', 'HipHop', 'Jazz', 'LoFi', 'Pop', 'PsychedelicRock', 'Punk', 'Reggae', 'Rock', 'Soul', 'Techno']

genres

['Blues',
 'Classical',
 'Country',
 'DeathMetal',
 'DoomMetal',
 'DrumNBass',
 'Electronic',
 'Folk',
 'Grime',
 'HeavyMetal',
 'HipHop',
 'Jazz',
 'LoFi',
 'Pop',
 'PsychedelicRock',
 'Punk',
 'Reggae',
 'Rock',
 'Soul',
 'Techno']

In [37]:
# Downsize image size from 300x300 to 224x224 for use in VGG16 model

from tensorflow.keras.preprocessing import image_dataset_from_directory
import numpy as np

train_data = np.array([])
test_data = np.array([])

data_dir = 'GAID'

for genre_folder in os.listdir(data_dir):
    genre_path = os.path.join(data_dir, genre_folder)
    if (os.path.isdir(genre_path)):
        genre_data_train, genre_data_test = image_dataset_from_directory(
            genre_path,
            labels=None,
            label_mode='int',
            class_names=None,
            color_mode='rgb',
            batch_size=32,
            image_size=(224, 224),
            shuffle=True,
            seed=47,
            validation_split=0.2,
            subset='both',
            interpolation='bilinear',
            follow_links=False,
            crop_to_aspect_ratio=False
        )

        train_data = np.append(train_data, genre_data_train)
        test_data = np.append(test_data, genre_data_test)






0
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.
Using 200 files for validation.
Found 1000 files belonging to 1 classes.
Using 800 files for training.


In [5]:
# import tensorflow as tf
# import numpy as np

# # Assuming 'GAID' is the base directory
# data_dir = "GAID"

# # Use validation_split to initially split the data
# full_dataset = tf.keras.preprocessing.image_dataset_from_directory(
#     data_dir,
#     labels='inferred',
#     label_mode='int',
#     class_names=genres,
#     color_mode='rgb',
#     batch_size=32,
#     image_size=(224, 224),
#     shuffle=True,  # Shuffle the data before splitting
#     seed=47,
#     validation_split=0.2,  # Use 20% for testing
#     subset='both',  # Load all data first
#     interpolation='bilinear',
# )

# # Separate the dataset into training and testing datasets
# train_dataset = full_dataset.take(int(0.8 * len(full_dataset)))
# test_dataset = full_dataset.skip(int(0.8 * len(full_dataset)))

# # Create a function to split each class (label) into 800 for training and 200 for testing randomly
# def custom_split(dataset, train_size=800, test_size=200):
#     # List to store the data after splitting
#     train_data = []
#     test_data = []
    
#     # Iterate over the dataset, split by class
#     for class_idx in range(len(genres)):  # Assuming genres is defined
#         # Get all images and labels for the current class
#         class_images = []
#         class_labels = []
#         for image, label in dataset:
#             if label == class_idx:
#                 class_images.append(image.numpy())
#                 class_labels.append(label.numpy())

#         # Shuffle the images and labels within the class
#         class_images = np.array(class_images)
#         class_labels = np.array(class_labels)
#         indices = np.arange(len(class_images))
#         np.random.shuffle(indices)
        
#         # Select first 800 for training and last 200 for testing
#         train_indices = indices[:train_size]
#         test_indices = indices[train_size:train_size + test_size]

#         # Append the selected images to the train and test datasets
#         train_data.append((class_images[train_indices], class_labels[train_indices]))
#         test_data.append((class_images[test_indices], class_labels[test_indices]))

#     # Convert the train and test data into TensorFlow datasets
#     train_images = np.concatenate([x[0] for x in train_data], axis=0)
#     train_labels = np.concatenate([x[1] for x in train_data], axis=0)
#     test_images = np.concatenate([x[0] for x in test_data], axis=0)
#     test_labels = np.concatenate([x[1] for x in test_data], axis=0)

#     # Create TensorFlow Dataset objects
#     train_dataset = tf.data.Dataset.from_tensor_slices((train_images, train_labels)).batch(32)
#     test_dataset = tf.data.Dataset.from_tensor_slices((test_images, test_labels)).batch(32)

#     return train_dataset, test_dataset

# # Apply the custom split function to the datasets
# train_dataset, test_dataset = custom_split(full_dataset)

# # Now you have the training and testing datasets


In [10]:
for data_point in data_train:
    print(data_point)


for data_point in data_test:
    print(data_point)

print(data_train)
print(data_test)

(<tf.Tensor: shape=(32, 224, 224, 3), dtype=float32, numpy=
array([[[[8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         [8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         [8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         ...,
         [7.30000000e+01, 3.80000000e+01, 3.40000000e+01],
         [7.30000000e+01, 3.80000000e+01, 3.40000000e+01],
         [7.30000000e+01, 3.80000000e+01, 3.40000000e+01]],

        [[8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         [8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         [8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         ...,
         [7.30000000e+01, 3.80000000e+01, 3.40000000e+01],
         [7.30000000e+01, 3.80000000e+01, 3.40000000e+01],
         [7.30000000e+01, 3.80000000e+01, 3.40000000e+01]],

        [[8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         [8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         [8.20000000e+01, 4.20000000e+01, 3.40000000e+01],
         ...,
         

In [ ]:
from keras.applications.vgg16 import VGG16
from keras.models import Model
from keras.layers import Dense

model = VGG16(include_top=False, input_shape=(200, 200, 3), pooling='max')

output = Dense(1, activation='sigmoid')(model.output)

for layer in model.layers[:12]:
    layer.trainable = False

final_model = Model(inputs=model.inputs, outputs=output)

final_model.compile(optimizer="sgd", loss="binary_crossentropy", metrics=["accuracy"])

final_model.fit(x_train, y_train, batch_size=128, epochs=5, validation_data=(x_test, y_test))

score = final_model.evaluate(x_test, y_test)
print(score)